<a href="https://colab.research.google.com/github/sarah1ibrahim/End-to-End-Echocardiographic-Analysis-Pipeline/blob/main/Video_Frame_Extraction.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Frames Extraction

In [ ]:
from google.colab import drive
import cv2
import pandas as pd
import os
import logging
import json
from datetime import datetime

# Mount Google Drive
if not os.path.exists('/content/drive/MyDrive'):
    print("[Info] Mounting Google Drive...")
    drive.mount('/content/drive')
else:
    print("[Info] Google Drive is already mounted.")

# Paths
video_dir = '/content/drive/MyDrive/✨ GP ✨/EchoNet_Dataset/EchoNet-Dynamic/Videos'
csv_file = '/content/drive/MyDrive/✨ GP ✨/EchoNet_Dataset/EchoNet-Dynamic/FileList.csv'
output_base_dir = '/content/drive/MyDrive/✨ GP ✨/EchoNet_Dataset/EchoNet-Dynamic/VideoFrames'
log_dir = '/content/drive/MyDrive/✨ GP ✨/EchoNet_Dataset/EchoNet-Dynamic/Logs'
processed_videos_file = '/content/drive/MyDrive/✨ GP ✨/EchoNet_Dataset/EchoNet-Dynamic/Logs/processed_videos.json'

# Create output and log directories
logger = logging.getLogger()
logger.setLevel(logging.INFO)
formatter = logging.Formatter('%(asctime)s [%(levelname)s] %(message)s')

# Console handler (prints to Colab output)
console_handler = logging.StreamHandler()
console_handler.setFormatter(formatter)
logger.addHandler(console_handler)

logger.info("Creating output directory if it doesn't exist...")
os.makedirs(output_base_dir, exist_ok=True)
logger.info(f"Output directory ensured: {output_base_dir}")

logger.info("Creating log directory if it doesn't exist...")
os.makedirs(log_dir, exist_ok=True)
logger.info(f"Log directory ensured: {log_dir}")

# Set up file logging
log_file = os.path.join(log_dir, f'frame_extraction_{datetime.now().strftime("%Y%m%d_%H%M%S")}.log')
file_handler = logging.FileHandler(log_file)
file_handler.setFormatter(formatter)
logger.addHandler(file_handler)

logger.info("Starting frame extraction script for missing videos...")

# Load CSV
logger.info(f"Loading CSV file from {csv_file}...")
try:
    df = pd.read_csv(csv_file)
except FileNotFoundError:
    logger.error(f"CSV file not found at {csv_file}. Please check the path and ensure the file exists.")
    raise
logger.info("CSV file loaded successfully.")

# Get list of videos from FileList.csv
video_names = df['FileName'].values
logger.info(f"Total videos in FileList.csv: {len(video_names)}")

# Load list of processed videos
processed_videos = set()
logger.info(f"Checking for processed videos file at {processed_videos_file}...")
if os.path.exists(processed_videos_file):
    logger.info("Processed videos file found. Loading...")
    with open(processed_videos_file, 'r') as f:
        processed_videos = set(json.load(f))
    logger.info(f"Loaded {len(processed_videos)} processed videos from {processed_videos_file}.")
else:
    logger.info("No processed videos file found. Starting fresh.")

# Identify remaining videos to process
logger.info("Identifying remaining videos to process...")
remaining_videos = [video_name for video_name in video_names if video_name not in processed_videos]
logger.info(f"Remaining videos to process: {len(remaining_videos)}")

# Batch processing
batch_size = 500  # Process 500 videos at a time
for batch_idx in range(0, len(remaining_videos), batch_size):
    batch_videos = remaining_videos[batch_idx:batch_idx + batch_size]
    logger.info(f"Processing batch {batch_idx // batch_size + 1} with {len(batch_videos)} videos...")

    for video_idx, video_name in enumerate(batch_videos, 1):
        logger.info(f"Processing video {batch_idx + video_idx}/{len(remaining_videos)}: {video_name}.avi")

        # Get the number of frames from FileList.csv
        video_row = df[df['FileName'] == video_name]
        if video_row.empty:
            logger.error(f"No matching row found in FileList.csv for {video_name}.avi. Skipping...")
            continue

        num_frames = int(video_row['NumberOfFrames'].values[0])
        logger.info(f"Expected number of frames: {num_frames}")

        # Check if the video file exists
        video_path = os.path.join(video_dir, f"{video_name}.avi")
        logger.info(f"Checking if video file exists at {video_path}...")
        if not os.path.exists(video_path):
            logger.error(f"Video file {video_path} not found. Skipping...")
            continue
        logger.info("Video file found.")

        # Create output directory for this video
        output_dir = os.path.join(output_base_dir, video_name)
        logger.info(f"Checking output directory {output_dir}...")
        if os.path.exists(output_dir):
            existing_frames = [f for f in os.listdir(output_dir) if f.endswith('.jpg')]
            if len(existing_frames) >= num_frames:
                logger.info(f"{len(existing_frames)} frames already exist in {output_dir}. Skipping extraction...")
                processed_videos.add(video_name)
                continue
            else:
                logger.info(f"Found {len(existing_frames)} frames, but expected {num_frames}. Re-extracting...")
                for f in existing_frames:
                    os.remove(os.path.join(output_dir, f))
        else:
            logger.info("Output directory does not exist. Creating...")
            os.makedirs(output_dir, exist_ok=True)
        logger.info(f"Output directory ready: {output_dir}")

        # Open video
        logger.info(f"Opening video {video_path}...")
        cap = cv2.VideoCapture(video_path)
        if not cap.isOpened():
            logger.error(f"Failed to open video {video_path}. Skipping...")
            continue
        logger.info("Video opened successfully.")

        # Get actual number of frames in the video
        actual_frame_count = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
        logger.info(f"Actual number of frames in video: {actual_frame_count}")
        if actual_frame_count < num_frames:
            logger.warning(f"Video has fewer frames ({actual_frame_count}) than expected ({num_frames}). Proceeding with available frames...")
            num_frames = actual_frame_count

        # Extract frames
        extracted_frames = 0
        frame_count = 0

        logger.info("Starting frame extraction...")
        while extracted_frames < num_frames:
            ret, frame = cap.read()
            if not ret:
                logger.warning(f"Video ended early at frame {frame_count}. Extracted {extracted_frames} frames.")
                break

            frame_file = os.path.join(output_dir, f"{video_name}_frame_{extracted_frames:04d}.jpg")
            success = cv2.imwrite(frame_file, frame)
            if not success:
                logger.error(f"Failed to write frame {frame_file}. Stopping extraction for this video...")
                break

            extracted_frames += 1
            frame_count += 1

        cap.release()

        if extracted_frames == num_frames:
            logger.info(f"Successfully extracted {extracted_frames} frames from {video_name}.avi")
        else:
            logger.warning(f"Extracted {extracted_frames} frames from {video_name}.avi, expected {num_frames}")

        # Add to processed videos
        processed_videos.add(video_name)

        # Save processed videos list after each video
        logger.info("Saving processed videos list...")
        with open(processed_videos_file, 'w') as f:
            json.dump(list(processed_videos), f)
        logger.info("Processed videos list saved.")

    logger.info(f"Completed batch {batch_idx // batch_size + 1}. Processed {len(processed_videos)} videos so far.")

logger.info("Frame extraction script completed.")

[Info] Mounting Google Drive...


INFO:root:Creating output directory if it doesn't exist...
2025-03-28 02:58:29,733 [INFO] Creating output directory if it doesn't exist...


Mounted at /content/drive


INFO:root:Output directory ensured: /content/drive/MyDrive/✨ GP ✨/EchoNet_Dataset/EchoNet-Dynamic/VideoFrames
2025-03-28 02:58:30,518 [INFO] Output directory ensured: /content/drive/MyDrive/✨ GP ✨/EchoNet_Dataset/EchoNet-Dynamic/VideoFrames
INFO:root:Creating log directory if it doesn't exist...
2025-03-28 02:58:30,522 [INFO] Creating log directory if it doesn't exist...
INFO:root:Log directory ensured: /content/drive/MyDrive/✨ GP ✨/EchoNet_Dataset/EchoNet-Dynamic/Logs
2025-03-28 02:58:30,538 [INFO] Log directory ensured: /content/drive/MyDrive/✨ GP ✨/EchoNet_Dataset/EchoNet-Dynamic/Logs
INFO:root:Starting frame extraction script for missing videos...
2025-03-28 02:58:31,139 [INFO] Starting frame extraction script for missing videos...
INFO:root:Loading CSV file from /content/drive/MyDrive/✨ GP ✨/EchoNet_Dataset/EchoNet-Dynamic/FileList.csv...
2025-03-28 02:58:31,147 [INFO] Loading CSV file from /content/drive/MyDrive/✨ GP ✨/EchoNet_Dataset/EchoNet-Dynamic/FileList.csv...
INFO:root:CSV

KeyboardInterrupt: 

# Video Folders and Frame Counts Verification

In [ ]:
from google.colab import drive
import pandas as pd
import os
from datetime import datetime
from tqdm import tqdm

# Mount Google Drive
if not os.path.exists('/content/drive/MyDrive'):
    print("[Info] Mounting Google Drive...")
    drive.mount('/content/drive')
else:
    print("[Info] Google Drive is already mounted.")

# Paths
csv_file = '/content/drive/MyDrive/EchoNet_Dataset/EchoNet-Dynamic/FileList.csv'
video_frames_dir = '/content/drive/MyDrive/EchoNet_Dataset/EchoNet-Dynamic/VideoFrames'

print("Starting frame verification script...")

# Load CSV
print(f"Loading CSV file from {csv_file}...")
try:
    df = pd.read_csv(csv_file)
except FileNotFoundError:
    print(f"[Error] CSV file not found at {csv_file}. Please check the path and ensure the file exists.")
    raise
print("CSV file loaded successfully.")

# Get total number of videos from FileList.csv
total_videos = len(df)
print(f"Total videos in FileList.csv: {total_videos}")

# Create a dictionary of video names and their expected frame counts
expected_frames = dict(zip(df['FileName'], df['NumberOfFrames'].astype(int)))
print(f"Loaded expected frame counts for {len(expected_frames)} videos.")

# Get list of frame folders
print(f"Listing frame folders in {video_frames_dir}...")
frame_folders = [folder for folder in os.listdir(video_frames_dir) if os.path.isdir(os.path.join(video_frames_dir, folder))]
num_frame_folders = len(frame_folders)
print(f"Found {num_frame_folders} frame folders.")

# Check if the number of frame folders matches the number of videos in FileList.csv
if num_frame_folders == total_videos:
    print(f"Number of frame folders matches the number of videos in FileList.csv: {num_frame_folders}/{total_videos} ✅")
else:
    print(f"[Warning] Mismatch in number of frame folders! Found {num_frame_folders}, expected {total_videos} based on FileList.csv. ⚠️")
    missing_folders = total_videos - num_frame_folders
    print(f"{missing_folders} videos are missing frame folders.")
    # List up to 10 missing videos
    missing_videos_list = [video for video in expected_frames.keys() if video not in frame_folders]
    print("Sample of missing videos:")
    for video in missing_videos_list[:10]:
        print(f" - {video}")
    if len(missing_videos_list) > 10:
        print(f"... and {len(missing_videos_list) - 10} more.")

# Proceed with detailed verification
print("\nProceeding with detailed frame count verification for each folder...")

# Initialize counters for summary
total_folders = num_frame_folders
correct_folders = 0
folders_with_issues = 0
missing_videos = 0

# List to store videos with incorrect frame counts
incorrect_videos = []

# Verify each folder with a progress bar
for folder_idx, folder_name in enumerate(tqdm(frame_folders, desc="Verifying folders", unit="folder")):
    print(f"Verifying folder {folder_idx + 1}/{total_folders}: {folder_name}")

    # Check if the folder name (video name) exists in the CSV
    if folder_name not in expected_frames:
        print(f"[Warning] Folder {folder_name} not found in FileList.csv. Skipping...")
        folders_with_issues += 1
        continue

    # Get expected number of frames
    expected_count = expected_frames[folder_name]
    print(f"Expected number of frames for {folder_name}: {expected_count}")

    # Count actual number of frames (jpg files) in the folder
    folder_path = os.path.join(video_frames_dir, folder_name)
    actual_frames = [f for f in os.listdir(folder_path) if f.endswith('.jpg')]
    actual_count = len(actual_frames)
    print(f"Actual number of frames in {folder_name}: {actual_count}")

    # Compare expected vs actual
    if actual_count == expected_count:
        print(f"Verification passed for {folder_name}: {actual_count}/{expected_count} frames.")
        correct_folders += 1
    else:
        print(f"[Error] Verification failed for {folder_name}: Found {actual_count} frames, expected {expected_count}.")
        folders_with_issues += 1
        incorrect_videos.append(folder_name)

# Check for videos in FileList.csv that don't have frame folders
missing_videos = len([video for video in expected_frames.keys() if video not in frame_folders])

# Summary
print("\n[Verification Summary]")
print(f"Total folders checked: {total_folders}")
print(f"Folders with correct frame counts: {correct_folders}")
print(f"Folders with issues: {folders_with_issues}")
print(f"Videos missing frame folders: {missing_videos}")
if incorrect_videos:
    print("Videos with incorrect frame counts:")
    for video in incorrect_videos:
        print(f" - {video}")
if folders_with_issues == 0 and missing_videos == 0:
    print("All folders have the correct number of frames! ✅")
else:
    print("Some issues were found during verification. Check the logs for details. ⚠️")

print("Frame verification script completed.")

[Info] Mounting Google Drive...
Mounted at /content/drive
Starting frame verification script...
Loading CSV file from /content/drive/MyDrive/EchoNet_Dataset/EchoNet-Dynamic/FileList.csv...
CSV file loaded successfully.
Total videos in FileList.csv: 10030
Loaded expected frame counts for 10030 videos.
Listing frame folders in /content/drive/MyDrive/EchoNet_Dataset/EchoNet-Dynamic/VideoFrames...
Found 10030 frame folders.
Number of frame folders matches the number of videos in FileList.csv: 10030/10030 ✅

Proceeding with detailed frame count verification for each folder...


Verifying folders:   0%|          | 0/10030 [00:00<?, ?folder/s]

Verifying folder 1/10030: 0X63CFF3F10BD4D1E8
Expected number of frames for 0X63CFF3F10BD4D1E8: 205


Verifying folders:   0%|          | 1/10030 [00:00<1:46:52,  1.56folder/s]

Actual number of frames in 0X63CFF3F10BD4D1E8: 205
Verification passed for 0X63CFF3F10BD4D1E8: 205/205 frames.
Verifying folder 2/10030: 0X5680EEA4E51CBF5E
Expected number of frames for 0X5680EEA4E51CBF5E: 201


...

Verifying folders: 100%|█████████▉| 10025/10030 [59:36<00:00, 30.90folder/s]

Actual number of frames in 0X7E06DB07314DEC7: 190
Verification passed for 0X7E06DB07314DEC7: 190/190 frames.
Verifying folder 10023/10030: 0X7DE5F4D17C87F518
Expected number of frames for 0X7DE5F4D17C87F518: 202
Actual number of frames in 0X7DE5F4D17C87F518: 202
Verification passed for 0X7DE5F4D17C87F518: 202/202 frames.
Verifying folder 10024/10030: 0X7DF5817CCA22438E
Expected number of frames for 0X7DF5817CCA22438E: 186
Actual number of frames in 0X7DF5817CCA22438E: 186
Verification passed for 0X7DF5817CCA22438E: 186/186 frames.
Verifying folder 10025/10030: 0X7E0ACE153EE2260F
Expected number of frames for 0X7E0ACE153EE2260F: 97
Actual number of frames in 0X7E0ACE153EE2260F: 97
Verification passed for 0X7E0ACE153EE2260F: 97/97 frames.
Verifying folder 10026/10030: 0X7DE8489883F940C7
Expected number of frames for 0X7DE8489883F940C7: 148
Actual number of frames in 0X7DE8489883F940C7: 148
Verification passed for 0X7DE8489883F940C7: 148/148 frames.
Verifying folder 10027/10030: 0X7DF4CD4

Verifying folders: 100%|██████████| 10030/10030 [59:36<00:00,  2.80folder/s]

Actual number of frames in 0X7DED63697C8793C1: 229
Verification passed for 0X7DED63697C8793C1: 229/229 frames.
Verifying folder 10029/10030: 0X7E08C6E04DE8DB0F
Expected number of frames for 0X7E08C6E04DE8DB0F: 285
Actual number of frames in 0X7E08C6E04DE8DB0F: 285
Verification passed for 0X7E08C6E04DE8DB0F: 285/285 frames.
Verifying folder 10030/10030: 0X7DE8BF9416439516
Expected number of frames for 0X7DE8BF9416439516: 192
Actual number of frames in 0X7DE8BF9416439516: 192
Verification passed for 0X7DE8BF9416439516: 192/192 frames.



[Verification Summary]
Total folders checked: 10030
Folders with correct frame counts: 10030
Folders with issues: 0
Videos missing frame folders: 0
All folders have the correct number of frames! ✅
Frame verification script completed.
